In [1]:
import json
import pandas as pd
import jieba
from jieba import posseg
import numpy as np
from loader import *
import pickle
import torch
from torch import nn
import sys
# from modules import embedding, encoder, model_sbj
from sklearn.model_selection import KFold

In [2]:
tensors = [[[1,2,3]], [[2,3,4], [5,6,7]]]

In [3]:
padding_three_d(tensors)

[[[1, 2, 3], [-9, -9, -9]], [[2, 3, 4], [5, 6, 7]]]

In [2]:
text_lists, _, result = loader.gen_test_data('../data/dev_data.json', get_answer=True, task=task)
        A, B, C = 1e-10, 1e-10, 1e-10
        for i in range(len(text_lists)):
            t = set(result[i])
            text = text_lists[i]
            R_i_tmp = deal_p_r(R_bound[i], R_vec[i], test_value=test_value)
            r = set()
            for r_i in R_i_tmp:
                sbj = ''.join(text[r_i[0][0]: r_i[0][1]+1])
                obj = ''.join(text[r_i[1][0]: r_i[1][1]+1])
                p = i2p[r_i[2]]
                r.add((sbj, p, obj))


            # p_set = set([r_i[1] for r_i in r])
            # if '妻子' in p_set and '丈夫' not in p_set:
            #     r_tmp = set([])
            #     for r_i in r:
            #         r_tmp.add(r_i)
            #         if r_i[1] == '妻子':
            #             r_tmp.add((r_i[2], '丈夫', r_i[0]))
            #     r = r_tmp
            # if '妻子' not in p_set and '丈夫' in p_set:
            #     r_tmp = set([])
            #     for r_i in r:
            #         r_tmp.add(r_i)
            #         if r_i[1] == '丈夫':
            #             r_tmp.add((r_i[2], '妻子', r_i[0]))
            #     r = r_tmp

            A += len(r & t)
            B += len(r)
            C += len(t)
        f1 = A * 2 / (B + C)
        precision = A / B
        recall = A / C
        print('spo model, f1:%.4f, precision:%.4f, recall:%.4f\n' % (f1, precision, recall))

1 [1 2 3]
2 [4 5 6]
3 [7 8 9]


In [11]:
with open('../data/p_dict.pkl', 'wb') as f:
    xxx = {'p2i': p2i, 'i2p': i2p}
    pickle.dump(xxx, f)

In [10]:
i2p

{0: '主演',
 1: '占地面积',
 2: '妻子',
 3: '出生日期',
 4: '海拔',
 5: '官方语言',
 6: '面积',
 7: '国籍',
 8: '作词',
 9: '出品公司',
 10: '邮政编码',
 11: '主角',
 12: '总部地点',
 13: '上映时间',
 14: '首都',
 15: '改编自',
 16: '创始人',
 17: '丈夫',
 18: '出版社',
 19: '号',
 20: '专业代码',
 21: '成立日期',
 22: '嘉宾',
 23: '祖籍',
 24: '注册资本',
 25: '修业年限',
 26: '字',
 27: '朝代',
 28: '父亲',
 29: '歌手',
 30: '所属专辑',
 31: '所在城市',
 32: '导演',
 33: '董事长',
 34: '作曲',
 35: '出生地',
 36: '目',
 37: '制片人',
 38: '编剧',
 39: '民族',
 40: '毕业院校',
 41: '主持人',
 42: '母亲',
 43: '人口数量',
 44: '作者',
 45: '简称',
 46: '连载网站',
 47: '气候',
 48: '身高'}

In [2]:
file_path = '../data/train_data.json'
a = gen_train_data_p(file_path)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.443 seconds.
Prefix dict has been built succesfully.


p, making sample_num:169802/173108, radio:0.9809


In [14]:
if []:
    print('x')

In [11]:
torch.Tensor([(0, 3), [2, 4]])

tensor([[0., 3.],
        [2., 4.]])

In [24]:
a[5][2]

[(9, 9)]

In [10]:
a[6][2]

[[0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0]]

In [6]:
def gen_train_data_ner(file_path, task):
    texts = []
    text_lists = []
    tag_lists = []
    spo_lists = []
    with open(file_path, 'r') as f:
        for line in f:
            tmp = json.loads(line)
            texts.append(tmp['text'])
            text_list, tag_list = list(zip(*posseg.lcut(tmp['text'], HMM=False)))
            text_list = list(text_list)
            tag_list = list(tag_list)
            text_lists.append(text_list)
            tag_lists.append(tag_list)
            spo_lists.append(tmp['spo_list'])

    if task == 'sbj':
        with open('../data/sbj_dict.pkl', 'rb') as f:
            ner2i = pickle.load(f)['sbj2i']
        ner1 = 'subject'
        ner1_type = 'subject_type'
    elif task == 'obj':
        with open('../data/obj_dict.pkl', 'rb') as f:
            ner2i = pickle.load(f)['obj2i']
        ner1 = 'object'
        ner1_type = 'object_type'
    else:
        assert 1 == -1

    r_text_lists = []
    r_tag_lists = []
    r_ners = []
    nums = 0
    for text, text_list, tag_list, spo_list in zip(texts, text_lists, tag_lists, spo_lists):
        text_len = len(text_list)
        ner = np.zeros(text_len)

        spo_extract = set()
        for spo in spo_list:
            ner_list, _ = list(zip(*posseg.lcut(spo[ner1], HMM=False)))
            ner_list = list(ner_list)
            ner_len = len(ner_list)
            for i in range(0, text_len-ner_len+1):
                if text_list[i: i+ner_len] == ner_list:
                    ner_s = i
                    ner_e = i + ner_len - 1
                    if ner_s == ner_e:
                        ner[ner_s] = ner2i[spo[ner1_type]]
                    elif ner_e - ner_s == 1:
                        ner[ner_s] = ner2i[spo[ner1_type]]
                        ner[ner_e] = ner2i[spo[ner1_type]] + 2
                    elif ner_e - ner_s > 1:
                        ner[ner_s] = ner2i[spo[ner1_type]]
                        ner[ner_s+1: ner_e] = ner2i[spo[ner1_type]] + 1
                        ner[ner_e] = ner2i[spo[ner1_type]] + 2
                    else:
                        print('wrong')
                        assert 1 == -1
                    spo_extract.add(spo[ner1])
        spo_exit = set([spo[ner1] for spo in spo_list])
        if len(spo_extract) != len(spo_exit):
            print(text)
            print(spo_exit)
            print(spo_extract)
            print()

In [26]:
jieba.del_word('中国共产党')
jieba.del_word('临清市')
jieba.del_word('江阴人')


In [27]:
print(jieba.lcut('朱黼  [清]字与村，号画亭，江苏江阴人', HMM=False))

['朱', '黼', ' ', ' ', '[', '清', ']', '字', '与', '村', '，', '号', '画', '亭', '，', '江苏', '江阴', '人']


In [7]:
gen_train_data_ner(file_path, 'obj')

李春英，女，汉族，1970年1月生，山东临清市人，大学，1992年7月参加工作，1999年6月加入中国共产党
{'汉族', '1970年1月', '中国', '山东临清'}
{'汉族', '1970年1月'}

黄强，男，汉族，1961年2月生，广东廉江人，1985年11月加入中国共产党，1976年10月参加工作，中山大学哲学系中国哲学专业，在职研究生学历，哲学博士
{'汉族', '中山大学', '广东廉江', '1961年2月'}
{'汉族', '广东廉江', '1961年2月'}

王润泽1，女，1983年10月生，山东人，2006年6月毕业于四川外语学院法语专业，现任云南边防总队昆明边防检查站正连职检查员，2007年12月至2008年8月和2009年6月至2010年5月，参加中国第六支、第八支赴海地维和警察防暴队，担任值勤官
{'1983年10月', '山东', '四川外语学院', '中国'}
{'1983年10月', '四川外语学院', '中国'}

《25岁前，我敢爱》是2008年知出版社出版的图书，作者是陆以心
{'知出版'}
set()

她出身楚国，芈姓，也称芈八子(八子为当时妃子的一个等级)，为秦国相穰侯魏冉之异父姊、后为秦惠文王妃，生子秦昭襄王
{'秦惠文王'}
set()

爱德华多·戈塔尔迪1985年7月22日出生于巴西，身高193厘米，惯用脚右脚，主要效力于莱里亚联盟俱乐部，场上位置门将
{'1985年7月22日', '193厘米'}
{'193厘米'}

张辉，女，心血管内科，汉族，1963年6月8日生，天津市人
{'汉族', '1963年6月8日', '天津市'}
{'汉族', '1963年6月8日'}

刘才光  男，1930年4月生，福建福州人
{'1930年4月', '福建福州'}
{'1930年4月'}

孙晓健，男，1964年9月出生，研究生学历，1986年2月加入中国共产党，现任泰兴市粮食系统党委副书记、副局长
{'中国', '1964年9月'}
{'1964年9月'}

彼得·盖布瑞尔（Peter Gabriel，1950年2月13日－）出生地是英国伦敦，是英国音乐家
{'1950年2月13日', '英国', '伦敦'}
{'1950年2月13日', '英国'}

《好好睡系列·今天和妈妈一起睡》是2010年二十一世纪出版

{'汉族', '1960年4月'}

作者简介：张天敏，女，中国作协会员，邓州市作协主席, 鲁迅文学院作家班结业，邓州市文化馆专业作家
{'中国', '鲁迅文学院'}
{'鲁迅文学院'}

关于牛角龙是一个独立属，还是某种成年三角龙或某个性别的三角龙目前存在争议
{'角龙目'}
set()

吴宏志，男，汉族，1969年10月出生，四川达州人，大学学历，1992年08月参加工作，1994年07月加入中国共产党，现任四川省农村信用社联合社绵阳办事处党委委员、纪委书记，射洪县人民政府副县长
{'汉族', '四川达州', '中国', '1969年10月'}
{'汉族', '四川达州', '1969年10月'}

李刚，男，汉族，1981年出生，山东莱芜人，博士，副教授，硕士生导师，东北大学秦皇岛分校经济学院副院长，金融工程研究所所长
{'汉族', '山东', '汉'}
{'汉族', '山东'}

王应麟：东汉三公，无出杨震、李固之右，而始进以邓、梁，君子以为疵
{'东汉', '汉'}
{'东汉'}

张俊驰骋江淮，平定淮宁，镇江、杭州、兰溪、秀州等地的武装割据势力，为南宋朝廷开辟了一席回旋之地
{'宋朝'}
set()

个人简介陆倩芳　女，1961年出生，陈卓林夫人，雅居乐地产控股有限公司董事局副主席、广州市房地产协会副会长、广东省侨心慈善基金会荣誉主席，祖籍中山市三乡镇鸦岗村，定居香港
{'1961年', '陈卓林', '陆倩芳'}
{'1961年', '陆倩芳'}

1999年至2006年，勇士队的变动不断，直到2006-07赛季，唐·尼尔森率领的金州勇士队依靠跑轰战术，在常规赛最后时刻爆发，搭上了季后赛的末班车
{'勇士'}
set()

个人简介丹斯里颜清文，祖籍福建省古田县吉巷乡昆山村，1932年8月28日出生于马来西亚霹雳州爱大华
{'福建省古田县吉巷乡昆山村', '1932年8月28日'}
{'福建省古田县吉巷乡昆山村'}

《贴身校花》改编自带玉小说《我的贴身校花》。该剧由搜狐视频、上海丝芭影视联合出品，于2016年3月正式开始，主要演员为SNH48张语格、李艺彤、吴哲晗、杨韫玉，赵顺然，经超等
{'张语格', '杨韫玉', '李艺彤', '吴哲晗', '赵顺然', '搜狐视频', '我的贴身校花', '带玉'}
{'张语格', '杨韫玉', '李艺彤'

”于是孙皓询问群臣，镇西大将军陆凯说道：“兵是不得已才用，三国鼎立一来，互相征伐，没有安定的时候，而今更是刚刚兼并巴蜀
{'三国'}
set()

季光，男，1968年8月生，汉族，江苏张家港市人，医学博士，教授、主任医师，博士研究生导师，1997年7月参加工作，1991年 1月加入中国共产党
{'汉族', '中国', '1968年8月'}
{'汉族', '1968年8月'}

周进生，字退之，1969年生于山东诸城，现供职于中国艺术研究院,,中国美术家协会会员，国家一级美术师，教授
{'山东诸城', '1969年', '中国', '中国艺术研究院'}
{'山东诸城', '1969年', '中国艺术研究院'}

人物生平早年经历北宋景德四年六月二十一日（1007年8月1日）寅时，欧阳修出生于绵州（今四川绵阳），当时他父亲任绵州军事推官5，已经56岁了
{'北宋', '1007年8月1日', '绵州'}
{'1007年8月1日', '绵州'}

厚壳树科，学名EHRETIACEAE，唇形目的一科
{'唇形目'}
set()

邓勇，男，汉族，1966年3月生，四川隆昌人，1992年1月加入中国共产党，1986年12月参加工作，中央党校在职研究生学历
{'1966年3月', '中国', '汉族', '中央党校', '四川隆昌'}
{'汉族', '四川隆昌', '中央党校', '1966年3月'}

艺术简介连乾坤，男，一九五四年生，河南开封市人，郑州大学毕业，中国书法家协会篆书研修班结业
{'郑州大学', '河南开封', '一九五四年'}
{'郑州大学', '一九五四年'}

《太白之风：陈望道传》2006年4月1日浙江人民出版社出版的图书，作者是周维强
{'浙江人民'}
set()

重走秋收之路2011年6月8日上午，随着开国元帅罗荣桓之子、中国人民解放军原二炮副政委罗东进将军的一声“出发”号令，由江西煤炭集团中鼎国际工程有限责任公司组织的“重走秋收起义革命道路”户外徒步活动正式启动
{'中国', '罗荣桓'}
{'罗荣桓'}

四、守财藏真，比干真人，宏德广化天尊比干出于子姓，为帝喾高辛氏之后，太始祖为“忠臣比干”，当时纣王无道，残害忠良
{'高辛'}
set()

2.李易峰，1987年5月4日出生于四川成都，中国内地男演员、流行乐歌手、影视制片人，2010年毕

叶强，男，1986年毕业于四川师范大学化学系，中学高级教师，四川省都江堰中学化学教师，2010届宏志班班主任，中国民主同盟盟员，都江堰市政协委员，四川省成都市劳动模范
{'中国', '四川师范大学'}
{'四川师范大学'}

《第二次爱你》是张敬轩演唱的一首粤语歌曲，由夏至作词，谢杰作曲，收录于2006年10月20日发行的专辑《笑忘书》中
{'夏至', '笑忘书', '谢杰', '张敬轩'}
{'夏至', '笑忘书', '张敬轩'}

吴忠兴 淳安县洋村乡石山底树人
{'淳安'}
set()

葆拉·贝伦·帕雷托（西班牙语：Paula Paretto），1986年1月16日出生于布宜诺斯艾利斯，阿根廷女子柔道运动员
{'布宜诺斯艾利斯', '1986年1月16日'}
{'布宜诺斯艾利斯'}

李飞毕业于华中科技大学，是中国科学院过程工程研究所副研究员
{'中国', '华中科技大学'}
{'华中科技大学'}

基本情况段建华，男，1980年生，河南省郸城县人，中国美术家协会会员，河南省美术家协会会员，江苏国画院特聘画家
{'中国', '1980年', '河南省郸城县'}
{'1980年', '河南省郸城县'}

《齿痕续爱》是在起点中文网上连载的综合类小说，作者是宛东
{'起点中文网', '宛东'}
{'宛东'}

王林，男，湖南长沙人，湖南知名专家、学者
{'湖南长沙'}
set()

个人资料周拾禄，字再中，1897年8月15日出生于浙江省义乌县佛堂镇丹墟村
{'1897年8月15日', '浙江省义乌'}
set()

沈赞清（1868—1943）字演公，又字雁潭，福建福州人
{'1868', '福建福州'}
{'1868'}

阿隆·布鲁克斯（Aaron Brooks），1985年1月14日出生于美国华盛顿州西雅图（Seattle, Washington），美国职业篮球运动员，司职控球后卫，效力于NBA明尼苏达森林狼队
{'1985年1月14日', '美国', '美国华盛顿州西雅图'}
{'美国', '美国华盛顿州西雅图'}

《魔幻都市第一季》是2013年播出的美国犯罪电视剧，由Edward Bianchi执导，杰弗里·迪恩·摩根 、 史蒂文·斯崔特等主演
{'Edward', '杰弗里·迪恩·摩根', '史蒂文·斯崔特'}
{'Edward', '杰弗里·迪

{'汉族', '湖北鄂州', '1967年10月'}

《椒房殿》是何晟铭演唱的歌曲，由于正作词，胡力作曲
{'于正', '胡力', '何晟铭'}
{'胡力', '何晟铭'}

吴青，女，1973年11月出生，海南海口人，汉族，大学学历，经济学学士学位，注册会计师，1995年8月参加工作，2009年7月加入中国共产党
{'1973年11月', '海南海口', '中国', '汉族', '汉'}
{'汉族', '海南海口', '1973年11月'}

北京市总工会副主席王永浩，男，1972年9月生，汉族，天津市人，1993年12月入党，1995年9月参加工作，北京农业工程大学水利机械专业大学毕业，在职研究生（中国农业大学农业机械化工程专业），工学博士，副教授
{'汉族', '中国', '1972年9月', '天津市'}
{'汉族', '1972年9月'}

雷法章（1903—1986），湖北汉川人，1921年毕业于华中大学文学院，旋即应聘入天津南开学校服务，任教务主任
{'湖北汉川', '1903', '华中大学'}
{'湖北汉川', '1903'}

阮宝欢于1951年参加中国民主同盟，后担任民盟番禺支部委员和支部主委
{'中国'}
set()

孙继海，1977年9月30日出生于辽宁省大连市，中国足球运动员，司职中后卫/边后卫/后腰等多个位置，是第一位在英超联赛中进球的中国球员
{'中国', '1977年9月30日', '辽宁省大连市'}
{'中国', '辽宁省大连市'}

《甜心先生》《甜心先生》是索尼影视娱乐公司出品的剧情片，由卡梅伦·克罗执导，汤姆·克鲁斯、蕾妮·齐薇格等主演，于1996年12月13日在美国上映
{'索尼影视娱乐公司', '1996年12月13日', '卡梅伦·克罗', '汤姆·克鲁斯'}
{'1996年12月13日', '卡梅伦·克罗', '汤姆·克鲁斯'}

王文，男，汉族，河南镇平人，1961年05月出生，现任江西省上饶市委常委1、中国人民解放军上饶军分区司令员2
{'汉族', '河南镇平', '中国'}
{'汉族', '河南镇平'}

《星运里的错》是2014年乔什·波恩执导的青少年浪漫爱情片，由谢琳·伍德蕾、安塞尔·埃尔格特等主演1，根据约翰·格林同名小说《无比美妙的痛苦》改编，讲述了两个患有癌症的青少年间有关爱情，生命和死亡的故事2

...

撒贝宁大家应该都很熟悉了，虽然没有朱军，崔永元，白岩松等的名气大， 可是人家的综艺节目，还有各大活动确实最活跃的的，堪称是中央电视台赚钱最多的男主持人，撒贝宁曾主持过《今日说法》，后来渐渐开始主持综艺节目，还担任了央视春晚的主持人，他每年的收入大概在1000万左右，这个数目是很高，但是和其他人比起来，他就是一个垫底的
{'撒贝宁', '央视'}
{'撒贝宁'}

周道富，男，汉族，1963年2月生，四川彭山人，1990年6月加入中国共产党，1980年12月参加工作，成都电讯工程学院应用物理专业毕业，大专学历
{'汉族', '中国', '四川彭山', '1963年2月'}
{'汉族', '四川彭山', '1963年2月'}

年8月6日中国武术散打王争霸赛第16周75公斤级的比赛中，浙江代表队的“玉面小达摩”郑裕蒿负于北京少林武校的“草原轿子”宝力高
{'中国'}
set()

紫滨鹬，属鹬科（Scolopacidae，snipes）是脊索动物门、脊椎动物亚门、鸟纲、鸻形目的1科
{'鸻形目'}
set()

《总是春天的日子》为韩国MBC电视台于2016年10月31日起播出的晨间连续剧，由《好运罗曼史》金庆熙、《金子轻松出来吧》李亨善导演与《10月美好的一天》金美京编剧共同打造的作品，由金昭惠、权贤尚、金敏京、姜星等主演
{'姜星', '金美京', '金敏京', '李亨善', '金昭惠', '权贤尚'}
{'金美京', '金敏京', '金昭惠', '李亨善', '权贤尚'}

黄莹，女，汉族，湖南湘潭人，经济学博士，厦门大学经济学院经济研究所助理教授，马克思主义学院、经济研究所助理教授，硕士生导师
{'湖南湘潭', '汉'}
set()

刘要萍，1969年生，山西太原人，现为中国书画家协会会员，山西省美术家协会会员、山西省工笔画协会会员，太原市美术家协会理事，傅山书画院院士
{'1969年', '太原', '中国'}
{'1969年', '中国'}

黄锦海1，男，1965年10月生，汉族，上海市人，大学本科，民革，1988年7月参加工作
{'汉族', '1965年10月', '上海市'}
{'汉族', '1965年10月'}

布兰登·阿姆斯特朗，1980年6月16日出生于加州旧金山，美国篮球运动员，司职后卫，2001年第1轮第23顺位被火箭选中，曾经效力新泽西

{'田青', '中国'}

邓蔚，男，汉族，1970年3月生，重庆人，1990年4月加入中国共产党，1987年10月参加工作，四川省委党校函院法律专业毕业，大学学历
{'汉族', '1970年3月', '中国', '四川省委党校'}
{'汉族', '1970年3月', '四川省委党校'}

《英雄联盟》是由海润影视制作出品的电视剧，林建中执导，周萌和王莹菲编剧，王挺、王珂、谢孟伟和王新等主演
{'王挺', '王莹菲', '海润影视', '周萌', '王珂', '谢孟伟', '王新', '林建中'}
{'王挺', '王莹菲', '周萌', '王珂', '谢孟伟', '王新', '林建中'}

小白菊别名钮扣菊，是菊科、菊目的二年生草本花卉，多年生草本，高至60cm
{'菊目'}
set()

《虎胆龙威5》是二十世纪福克斯公司出品的一部动作片，由约翰·摩尔执导，布鲁斯·威利斯、杰·科特尼、玛丽·伊丽莎白·文斯蒂德、阿莫瑞·诺拉斯克等主演
{'布鲁斯·威利斯', '约翰·摩尔'}
{'布鲁斯·威利斯'}

李光地（1642年-1718年），字晋卿，号厚庵，别号榕村，福建泉州人，清朝康熙年间大臣、理学名臣
{'福建泉州', '1642年', '清朝', '榕村', '晋卿', '厚庵'}
{'1642年', '清朝', '榕村', '晋卿', '厚庵'}

《西京故事》是由西安曲江丫丫影视文化股份有限公司出品，姚远执导，张国强、陈小艺领衔主演的温情励志剧1
{'姚远', '丫丫影视', '陈小艺', '张国强'}
{'姚远', '陈小艺', '张国强'}

黎觉行，男，汉族，1971年12月出生，海南乐东人，1992年9月参加工作，1999年6月加入中国共产党，大学学历，工学学士学位，助理工程师
{'汉族', '1971年12月', '中国', '海南乐东'}
{'汉族', '1971年12月', '海南乐东'}

林宏宇，男，生于1968年，福建人
{'1968年', '福建'}
{'1968年'}

利特曼，德国人，马格德堡队，身高181厘米，场上位置：后卫，惯用脚：右脚，代表国家队：出场0次，进0球，欧洲三大杯：出场0次，进0球，欧洲冠军联赛：出场0次，进0球
{'181厘米', '德国'}
{'181厘米'}

张连璋，男，1968年4月出生，籍贯江苏泰兴，199

《心的锻炼禅修的观念与方法》是2011年世界知识出版社出版的图书，作者是释继程
{'世界知识'}
set()

北京中视大观书画院是于2016年6月经上级主管部门批准在京成立的1，从事书画创作、研究、展览、培训、鉴定、收藏、交流等活动的公益性组织，总部地址设在北京，在全国各省、直辖市、自治区成立分院
{'2016年6月'}
set()

吉宗沅（1761—1843）：字盈科、号跛牂，江苏镇江人
{'盈科', '1761', '江苏镇江'}
{'盈科', '1761'}

唐滤晶，1989年2月4日出生于湖南省，毕业于中央戏剧学院2008级表演系3班，中国内地男演员1
{'湖南省', '1989年2月4日', '中央戏剧学院'}
{'湖南省', '中央戏剧学院'}

钟敬尧，男，1966年7月生，汉族，广东梅州市梅江区人，1986年12月参加工作，1989年7月加入中国共产党，在职大学学历，现任梅州市职业技术学校（市旅游职业技术学校）校长（正科），确定为梅州市职业技术学校（市旅游职业技术学校）校长（副处）人选考察对象
{'汉族', '中国', '1966年7月', '广东梅州市'}
{'汉族', '1966年7月', '广东梅州市'}

《美国宪法上的正当法律程序》是2007年黑龙江人民出版社出版的图书，作者是丁玮
{'黑龙江人民', '丁玮'}
{'丁玮'}

《赵匡胤》由中国台湾著名导演余汉祥执导，狄珊编剧，由叶青、林美照、狄莺、杨怀民、连明月、陈松勇、海野武沙、林梦梅等领衔主演
{'陈松勇', '中国台湾', '海野武沙', '林美照', '中国', '连明月', '狄莺', '余汉祥', '杨怀民', '叶青', '林梦梅', '狄珊', '汉'}
{'陈松勇', '中国台湾', '海野武沙', '林美照', '连明月', '狄莺', '余汉祥', '杨怀民', '叶青', '林梦梅', '狄珊', '汉'}

所罗门·希尔（Solomon Hill），1991年3月28日出生于美国加利福尼亚州洛杉矶（Los Angeles, California），美国职业篮球运动员，司职小前锋，效力于NBA新奥尔良鹈鹕队
{'美国', '1991年3月28日', '美国加利福尼亚州洛杉矶'}
{'美国', '美国加利福尼亚州洛杉矶'}

雷立柏教授1967年生于奥地利，1


陈少荣，男，汉族，1968年11月生，广东陆丰人，1991年7月参加工作，1993年11月加入中国共产党，广东省社科院在职研究生学历
{'广东陆丰', '广东省社科院', '中国', '汉族', '1968年11月'}
{'汉族', '广东省社科院', '广东陆丰', '1968年11月'}

胡凌云，男，汉族，1952年10月生，重庆市人，1968年11月参加工作，1975年加入中国共产党，南京工学院（现东南大学）计算机科学与工程系计算机专业1982年毕业，大学本科学历，研究员
{'南京工学院', '重庆', '1952年10月', '汉'}
{'南京工学院', '1952年10月'}

《驯鹿游戏》是由约翰·弗兰克海默执导，本·阿弗莱克、查理兹·塞隆等主演的剧情片
{'查理兹·塞隆', '约翰·弗兰克海默', '本·阿弗莱克'}
{'查理兹·塞隆', '本·阿弗莱克'}

宋石雨，女，1982年6月出生，汉族，大学文化，江苏徐州人
{'汉族', '江苏徐州', '1982年6月'}
{'汉族', '1982年6月'}

姓名：侯玲林  工作分工：侯玲林，男，汉族，1955年11月生，湖南人，1988年4月加入中国共产党，1973年3月参加工作，中国社科院研究生院财贸系商业管理专业毕业，硕士研究生学历
{'汉族', '中国', '1955年11月'}
{'汉族', '1955年11月'}

《如果蜗牛有爱情》是由企鹅影业和东阳正午阳光影视有限公司联合出品，张开宙执导，朱朱编剧，王凯、王子文、徐悦、于恒等主演的爱情推理剧
{'于恒', '王凯', '张开宙', '王子文', '朱朱', '企鹅影业', '东阳正午阳光影视有限公司', '徐悦'}
{'王凯', '张开宙', '王子文', '朱朱', '企鹅影业', '东阳正午阳光影视有限公司', '徐悦'}

《心血管病免疫学》是2008年科学出版社出版的一本图书，作者是廖玉华，沈关心，龚非力
{'沈关心', '科学', '龚非力', '廖玉华'}
{'沈关心', '龚非力', '廖玉华'}

姓名： 兰保景出生地： 山西籍贯： 山西简介： 汉族，1935年8月生，山西原平人，1953年12月加入中国共产党，1949年9月参加革命工作，天津社会科学进修学院哲学专业毕业，大专学历，中将军衔
{'汉族', '中国', 

{'柳城县马山乡', '中国'}
{'柳城县马山乡'}

卞学宝，男，汉族，1961年7月出生，江苏扬州人
{'汉族', '江苏扬州'}
{'汉族'}

183club，中国台湾流行乐男子组合，由王少伟、颜行书、明道、黄玉荣、祝钒刚组成
{'中国'}
set()

王启林，男，汉族，生于1955年11月，遂宁市安居区人，党函大学，1975年9月参加工作，1978年3月加入中国共产党
{'汉族', '中国', '1955年11月', '遂宁市安居区'}
{'汉族', '1955年11月', '遂宁市安居区'}

安妮卡·苏赫尔，女，1990年4月3日出生于德国，是一名女子现代五项运动员
{'德国', '1990年4月3日'}
{'德国'}

韩玉心，女，朝鲜人，1991年1月10日出生，身高：182cm,体重：67kg
{'1991年1月10日', '182cm', '朝鲜'}
{'1991年1月10日', '182cm'}

于果，Hugo，原名于海波，男，汉族，1982年4月16日出生于内蒙古自治区通辽市，毕业于意大利米兰理工学院，极合空间规划设计（北京）有限公司创始人兼设计总监
{'内蒙古自治区通辽市', '汉族', '意大利米兰理工学院', '1982年4月16日', '汉'}
{'汉族', '意大利米兰理工学院', '内蒙古自治区通辽市'}

安德烈·道金斯（Andre Dawkins），1991年9月19日出生于美国弗吉尼亚州切萨皮克（Chesapeake, Virginia），美国职业篮球运动员，司职得分后卫，效力于NBA波士顿凯尔特人队
{'1991年9月19日', '美国弗吉尼亚州切萨皮克'}
{'美国弗吉尼亚州切萨皮克'}

加里·佩顿（Gary Payton），1968年7月23日出生于美国加利福尼亚州奥克兰（Oakland·CA），前美国职业篮球运动员，司职控球后卫，绰号“手套”（The Glove）1
{'1968年7月23日', '美国', '美国加利福尼亚州奥克兰'}
{'美国', '美国加利福尼亚州奥克兰'}

韩雪，2010年与冯巩合作在春节晚会表演《不能让他走》，韩雪的美貌不用多说，关键智商也高，韩雪是文化考试第一名的成绩被上海戏剧学院表演系录取的
{'上海戏剧学院'}
set()

甘强，男，汉族，1971年8月生，广西龙州人，2

In [10]:
nums / all_nums

0.04342953531899161

In [9]:
all_nums

173108

In [3]:
a = gen_train_data_spo(file_path)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.441 seconds.
Prefix dict has been built succesfully.


spo make samples, nums:191739/196864, radio:0.9740


In [5]:
for i_list in a[4]:
    for i in i_list:
        if i >= 50:
            print(i_list)

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 6.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 65.0, 0.0, 0.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 23.0, 0.0, 0.0, 23.0, 0.0, 0.0, 0.0, 0.0, 0.0, 77.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 65.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 39.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 38.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 32.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 39.0, 0.0, 0.0, 0.0, 0.0, 0.0, 53.0, 0.0, 0.0, 5.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 77.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

[72.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 70.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 32.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 72.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

In [2]:
im

TypeError: 'set' object does not support indexing

In [25]:
    with open('../data/p_dict.pkl', 'rb') as f:
        i2s = pickle.load(f)

In [26]:
i2s

{'p2i': {'丈夫': 1,
  '歌手': 2,
  '占地面积': 3,
  '邮政编码': 4,
  '国籍': 5,
  '出品公司': 6,
  '出版社': 7,
  '注册资本': 8,
  '上映时间': 9,
  '民族': 10,
  '目': 11,
  '所在城市': 12,
  '创始人': 13,
  '成立日期': 14,
  '祖籍': 15,
  '导演': 16,
  '制片人': 17,
  '气候': 18,
  '修业年限': 19,
  '连载网站': 20,
  '主持人': 21,
  '父亲': 22,
  '主演': 23,
  '人口数量': 24,
  '总部地点': 25,
  '简称': 26,
  '作词': 27,
  '作者': 28,
  '首都': 29,
  '号': 30,
  '董事长': 31,
  '所属专辑': 32,
  '朝代': 33,
  '专业代码': 34,
  '毕业院校': 35,
  '嘉宾': 36,
  '海拔': 37,
  '出生地': 38,
  '出生日期': 39,
  '妻子': 40,
  '字': 41,
  '身高': 42,
  '作曲': 43,
  '主角': 44,
  '官方语言': 45,
  '面积': 46,
  '改编自': 47,
  '母亲': 48,
  '编剧': 49},
 'i2p': {1: '丈夫',
  2: '歌手',
  3: '占地面积',
  4: '邮政编码',
  5: '国籍',
  6: '出品公司',
  7: '出版社',
  8: '注册资本',
  9: '上映时间',
  10: '民族',
  11: '目',
  12: '所在城市',
  13: '创始人',
  14: '成立日期',
  15: '祖籍',
  16: '导演',
  17: '制片人',
  18: '气候',
  19: '修业年限',
  20: '连载网站',
  21: '主持人',
  22: '父亲',
  23: '主演',
  24: '人口数量',
  25: '总部地点',
  26: '简称',
  27: '作词',
  28: '作者',
  29: '首都',
  30: 

In [2]:
def gen_train_data_sbj(file_path):
    sbj_dict = get_type_dict_sbj()
    texts = []
    text_lists = []
    tag_lists = []
    spo_lists = []
    with open(file_path, 'r') as f:
        for line in f:
            tmp = json.loads(line)
            texts.append(tmp['text'])
            text_list, tag_list = list(zip(*posseg.lcut(tmp['text'], HMM=False)))
            text_list = list(text_list)
            tag_list = list(tag_list)
            text_lists.append(text_list)
            tag_lists.append(tag_list)
            spo_lists.append(tmp['spo_list'])

    with open('../data/sbj_dict.pkl', 'rb') as f:
        sbj2i = pickle.load(f)['sbj2i']

    r_text_lists = []
    r_tag_lists = []
    r_sbjs = []
    nums = 0
    for text_list, tag_list, spo_list in zip(text_lists, tag_lists, spo_lists):
        text_len = len(text_list)
        sbj = np.zeros(text_len)

        spo_extract = set()
        for spo in spo_list:
            sbj_list, _ = list(zip(*posseg.lcut(spo['subject'], HMM=False)))
            sbj_list = list(sbj_list)
            sbj_len = len(sbj_list)
            for i in range(0, text_len-sbj_len+1):
                if text_list[i: i+sbj_len] == sbj_list:
                    sbj_s = i
                    sbj_e = i + sbj_len - 1
                    xxx = sbj_dict[spo['subject_type']]
                    if sbj_s == sbj_e:
                        sbj[sbj_s] = sbj2i[xxx]
                    elif sbj_e - sbj_s == 1:
                        sbj[sbj_s] = sbj2i[xxx]
                        sbj[sbj_e] = sbj2i[xxx] + 2
                    elif sbj_e - sbj_s > 1:
                        sbj[sbj_s] = sbj2i[xxx]
                        sbj[sbj_s+1: sbj_e] = sbj2i[xxx] + 1
                        sbj[sbj_e] = sbj2i[xxx] + 2
                    else:
                        print('wrong')
                        assert 1 == -1
                    spo_extract.add(spo['subject'])
        nums += len(spo_extract)
        if len(spo_extract) != 0:
            r_text_lists.append(text_list)
            r_tag_lists.append(tag_list)
            r_sbjs.append(sbj.tolist())

    all_nums = 0
    for spo_list in spo_lists:
        all_nums += len(set([spo['subject'] for spo in spo_list]))

    print('sbj, make samples_num:%d, sbj_nums:%d/%d, radio:%.4f' % (len(r_text_lists), nums, all_nums, nums/all_nums))

    return r_text_lists, r_tag_lists, r_sbjs

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.449 seconds.
Prefix dict has been built succesfully.


sbj, make samples_num:172333, sbj_nums:195042/196864, radio:0.9907


In [37]:
'a[2][23]我靠dsaAS'.lower()

'a[2][23]我靠dsaas'

In [35]:
spo_lists = spo_list
all_nums = 0
for spo_list in spo_lists:
    all_nums += len([spo['subject'] for spo in spo_list])

print('sbj, make samples_num:%d, sbj_nums:%d/%d, radio:%.4f' % (len(texts), nums, all_nums, nums/all_nums))

sbj, make samples_num:173109, sbj_nums:361242/364218, radio:0.9918


In [ ]:
words = [jieba.lcut(item['word'], HMM=False) for item in tmp['postag']]